In [1]:
!pip install transformers

In [2]:
from transformers import pipeline

### For text summarization

In [3]:
summarizer = pipeline('summarization')

No model was supplied, defaulted to sshleifer/distilbart-cnn-12-6 (https://huggingface.co/sshleifer/distilbart-cnn-12-6)


In [4]:
text = """ New York (CNN)When Liana Barrientos was 23 years old, she got married in Westchester County, New York.
... A year later, she got married again in Westchester County, but to a different man and without divorcing her first husband.
... Only 18 days after that marriage, she got hitched yet again. Then, Barrientos declared "I do" five more times, sometimes only within two weeks of each other.
... In 2010, she married once more, this time in the Bronx. In an application for a marriage license, she stated it was her "first and only" marriage.
... Barrientos, now 39, is facing two criminal counts of "offering a false instrument for filing in the first degree," referring to her false statements on the
... 2010 marriage license application, according to court documents.
... Prosecutors said the marriages were part of an immigration scam.
... On Friday, she pleaded not guilty at State Supreme Court in the Bronx, according to her attorney, Christopher Wright, who declined to comment further.
... After leaving court, Barrientos was arrested and charged with theft of service and criminal trespass for allegedly sneaking into the New York subway through an emergency exit, said Detective
... Annette Markowski, a police spokeswoman. In total, Barrientos has been married 10 times, with nine of her marriages occurring between 1999 and 2002.
... All occurred either in Westchester County, Long Island, New Jersey or the Bronx. She is believed to still be married to four men, and at one time, she was married to eight men at once, prosecutors say.
... Prosecutors said the immigration scam involved some of her husbands, who filed for permanent residence status shortly after the marriages.
... Any divorces happened only after such filings were approved. It was unclear whether any of the men will be prosecuted.
... The case was referred to the Bronx District Attorney\'s Office by Immigration and Customs Enforcement and the Department of Homeland Security\'s
... Investigation Division. Seven of the men are from so-called "red-flagged" countries, including Egypt, Turkey, Georgia, Pakistan and Mali.
... Her eighth husband, Rashid Rajput, was deported in 2006 to his native Pakistan after an investigation by the Joint Terrorism Task Force.
... If convicted, Barrientos faces up to four years in prison.  Her next court appearance is scheduled for May 18.
... """

In [5]:
print(summarizer(text, max_length=150, min_length=50, do_sample=False))

[{'summary_text': ' Liana Barrientos, 39, is charged with two counts of "offering a false instrument for filing in the first degree" In total, she has been married 10 times, with nine of her marriages occurring between 1999 and 2002 . At one time, she was married to eight men at once, prosecutors say .'}]


### For Context based question answering

In [6]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, pipeline

model_name = "deepset/roberta-base-squad2"

nlp = pipeline('question-answering', model=model_name, tokenizer=model_name)
QA_input = {
    'question': 'Why is model conversion important?',
    'context': 'The option to convert models between FARM and transformers gives freedom to the user and let people easily switch between frameworks.'
}
res = nlp(QA_input)

In [7]:
print(res)

{'score': 0.21171443164348602, 'start': 59, 'end': 84, 'answer': 'gives freedom to the user'}


### Using gradio

In [8]:
!pip install gradio

In [9]:
import gradio as gr

examples = [
        [   'Question-Answer',
             '',
            'The option to convert models between FARM and transformers gives freedom to the user and let people easily switch between frameworks.',
            'Why is model conversion important?'
         ],
        [   'Question-Answer',
             '',
            "The Amazon rainforest is a moist broadleaf forest that covers most of the Amazon basin of South America", 
            "Which continent is the Amazon rainforest in?"
        ],
        [   'Question-Answer',
             '',
            'I am a Programmer.',
            'Who am I?' 
        ]
    ]

def summarize_text(text):
    summary = summarizer(text, max_length=130, min_length=30, do_sample=False)
    summary = summary[0]['summary_text']
    return summary

def question_answer(context, question):
    QA_input = {
        'context': context,
        'question': question
    }
    res = nlp(QA_input)
    return (res['answer'])

def home_func(model_choice, summ_text, qa_context, qa_question):
    if model_choice=="Text Summarizer":
        if summ_text == "":
            return "Input correct text to be summarized"
        return summarize_text(summ_text)
    elif model_choice=="Question-Answer":
        if qa_context == "" or qa_question == "":
            return "Choose correct Context and associated questions"
              
        return question_answer(qa_context, qa_question) 


### Check of above function

In [11]:
print(home_func("Question-Answer", "", examples[1][2], examples[1][3]))
print(home_func("Text Summarizer", text, "", ""))

South America
 Liana Barrientos, 39, is charged with two counts of "offering a false instrument for filing in the first degree" In total, she has been married 10 times, with nine of her marriages occurring between 1999 and 2002 . At one time, she was married to eight men at once, prosecutors say .


In [14]:
iface = gr.Interface(fn = home_func, 
                     inputs = [gr.inputs.Dropdown(["Text Summarizer", "Question-Answer"], type="value"), 
                               gr.inputs.Textbox(lines=5, placeholder="Enter your text here...", label="Text to be summarized"),
                               gr.inputs.Textbox(lines=5, placeholder="Choose from examples", label="Context"),
                               gr.inputs.Textbox(lines=5, placeholder="Choose from examples", label="Question")],
                     outputs="text",
                     examples=examples)

In [15]:
iface.launch()

Running on local URL:  http://127.0.0.1:7861/

To create a public link, set `share=True` in `launch()`.


(<Flask 'gradio.networking'>, 'http://127.0.0.1:7861/', None)